In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from pathlib import Path

try:
    from google.colab import drive

    drive.mount("/content/drive")
    workding_dir = "/content/drive/MyDrive/logical-reasoning/"
except ModuleNotFoundError:
    workding_dir = str(Path.cwd().parent)

In [3]:
import os
import sys
from pathlib import Path

os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /home/inflaton/code/projects/courses/logical-reasoning


In [4]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /home/inflaton/code/projects/courses/logical-reasoning/.env


True

In [5]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("LOGICAL_REASONING_DATA_PATH")
results_path = os.getenv("LOGICAL_REASONING_RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"

print(model_name, adapter_name_or_path, load_in_4bit, data_path, results_path)

internlm/internlm2_5-7b-chat-1m inflaton-ai/InternLM_2_5-7b_LoRA-Adapter True datasets/mgtv results/mgtv-results_internlm_4bit.csv


In [16]:
%%time
os.environ["TOKENIZERS_PARALLELISM"] = "true"

!python --version
!pip show transformers

Python 3.11.9
Name: transformers
Version: 4.43.0.dev0
Summary: State-of-the-art Machine Learning for JAX, PyTorch and TensorFlow
Home-page: https://github.com/huggingface/transformers
Author: The Hugging Face team (past and future) with the help of all our contributors (https://github.com/huggingface/transformers/graphs/contributors)
Author-email: transformers@huggingface.co
License: Apache 2.0 License
Location: /home/inflaton/miniconda3/envs/llama-factory/lib/python3.11/site-packages
Requires: filelock, huggingface-hub, numpy, packaging, pyyaml, regex, requests, safetensors, tokenizers, tqdm
Required-by: llamafactory, peft, trl, vllm
CPU times: user 121 ms, sys: 61.4 ms, total: 183 ms
Wall time: 4.8 s


In [7]:
from llm_toolkit.llm_utils import *
from llm_toolkit.logical_reasoning_utils import *

device = check_gpu()

loading /home/inflaton/code/projects/courses/logical-reasoning/llm_toolkit/logical_reasoning_utils.py
GPU is available


In [8]:
%%time

model, tokenizer = load_model(model_name, adapter_name_or_path=adapter_name_or_path, load_in_4bit=load_in_4bit, using_llama_factory=False)

loading model: internlm/internlm2_5-7b-chat-1m with adapter: inflaton-ai/InternLM_2_5-7b_LoRA-Adapter


Loading checkpoint shards:   0%|          | 0/8 [00:00<?, ?it/s]

adapter_config.json:   0%|          | 0.00/679 [00:00<?, ?B/s]

adapter_model.safetensors:   0%|          | 0.00/37.8M [00:00<?, ?B/s]

CPU times: user 2min 18s, sys: 9min 43s, total: 12min 2s
Wall time: 1h 41min 28s


In [9]:
datasets = load_logical_reasoning_dataset(
    data_path,
    tokenizer=tokenizer,
    chinese_prompt=not use_english_datasets,
    using_p1=False,
)

loading train/test data files


Map:   0%|          | 0/25000 [00:00<?, ? examples/s]

Map:   0%|          | 0/3000 [00:00<?, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth', 'train_text', 'prompt'],
        num_rows: 25000
    })
    test: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth', 'train_text', 'prompt'],
        num_rows: 3000
    })
})


In [10]:
import numpy as np


def evaluate_model_with_repetition_penalty(
    model,
    tokenizer,
    model_name,
    dataset,
    start_repetition_penalty=1.0,
    end_repetition_penalty=1.15,
    step_repetition_penalty=0.01,
):
    print(f"Evaluating model: {model_name} on {device}")

    for repetition_penalty in np.arange(
        start_repetition_penalty,
        end_repetition_penalty + step_repetition_penalty,
        step_repetition_penalty,
    ):
        print(f"*** Evaluating with repetition_penalty: {repetition_penalty}")
        predictions = eval_model(
            model,
            tokenizer,
            dataset,
            device=device,
            repetition_penalty=repetition_penalty,
            max_new_tokens=8,
        )

        model_name_with_rp = f"{model_name}_4bit_rp{repetition_penalty}"

        save_results(
            model_name_with_rp,
            results_path,
            dataset,
            predictions,
            debug=True,
        )

        metrics = calc_metrics(dataset["label"], predictions, debug=False)
        print(metrics)

In [11]:
%%time

evaluate_model_with_repetition_penalty(model, tokenizer, model_name, datasets["test"])

Evaluating model: internlm/internlm2_5-7b-chat-1m on cuda
*** Evaluating with repetition_penalty: 1.0


  0%|          | 1/3000 [00:17<14:45:44, 17.72s/it]

--------
step 1: 不是
--------
step 2: 不是
--------
step 3: 不是
--------
step 4: 不是
--------
step 5: 不是


100%|██████████| 3000/3000 [2:23:40<00:00,  2.87s/it]  


      text label title                                             puzzle  \
0  甄加索是自杀吗    不是  海岸之谜  在远离城市喧嚣的海边小屋，一天清晨，邻居发现甄加索僵卧在沙滩上，已无生命迹象。现场没有发现任...   

                                               truth  \
0  甄加索是一位热爱自然的画家，他每年都会来到这个海边小屋寻找灵感。在他生命的最后几天，他一直在...   

  internlm/internlm2_5-7b-chat-1m_4bit_rp1.0  
0                                         不是  
{'accuracy': 0.783}
*** Evaluating with repetition_penalty: 1.01


...

      text label title                                             puzzle  \
0  甄加索是自杀吗    不是  海岸之谜  在远离城市喧嚣的海边小屋，一天清晨，邻居发现甄加索僵卧在沙滩上，已无生命迹象。现场没有发现任...   

                                               truth  \
0  甄加索是一位热爱自然的画家，他每年都会来到这个海边小屋寻找灵感。在他生命的最后几天，他一直在...   

  internlm/internlm2_5-7b-chat-1m_4bit_rp1.0  \
0                                         不是   

  internlm/internlm2_5-7b-chat-1m_4bit_rp1.01  \
0                                          不是   

  internlm/internlm2_5-7b-chat-1m_4bit_rp1.02  \
0                                          不是   

  internlm/internlm2_5-7b-chat-1m_4bit_rp1.03  \
0                                          不是   

  internlm/internlm2_5-7b-chat-1m_4bit_rp1.04  \
0                                          不是   

  internlm/internlm2_5-7b-chat-1m_4bit_rp1.05  \
0                                          不是   

  internlm/internlm2_5-7b-chat-1m_4bit_rp1.06  \
0                                          不是   

  internlm/internlm2_5-7b-chat-1m_4bit_rp

  0%|          | 1/3000 [00:01<51:49,  1.04s/it]

--------
step 1: 不是
--------
step 2: 不是
--------
step 3: 不是
--------
step 4: 不是
--------
step 5: 不是


100%|██████████| 3000/3000 [53:06<00:00,  1.06s/it] 


      text label title                                             puzzle  \
0  甄加索是自杀吗    不是  海岸之谜  在远离城市喧嚣的海边小屋，一天清晨，邻居发现甄加索僵卧在沙滩上，已无生命迹象。现场没有发现任...   

                                               truth  \
0  甄加索是一位热爱自然的画家，他每年都会来到这个海边小屋寻找灵感。在他生命的最后几天，他一直在...   

  internlm/internlm2_5-7b-chat-1m_4bit_rp1.0  \
0                                         不是   

  internlm/internlm2_5-7b-chat-1m_4bit_rp1.01  \
0                                          不是   

  internlm/internlm2_5-7b-chat-1m_4bit_rp1.02  \
0                                          不是   

  internlm/internlm2_5-7b-chat-1m_4bit_rp1.03  \
0                                          不是   

  internlm/internlm2_5-7b-chat-1m_4bit_rp1.04  ...  \
0                                          不是  ...   

  internlm/internlm2_5-7b-chat-1m_4bit_rp1.06  \
0                                          不是   

  internlm/internlm2_5-7b-chat-1m_4bit_rp1.07  \
0                                          不是   

  internlm/internlm2_5-7b-chat-